# Backtesting with NautilusTrader

---

In this notebook, I'll experiment with a simple backtesting strategy using the **`NautilusTrader`** library. The strategy will be tested on **Bitcoin/USD 1-hour interval data**. This workflow will demonstrate how to set up, implement, and evaluate a trading strategy using historical data.

## High-level API

The high-level API centers around a **`BacktestNode`**, which orchestrates the management of multiple `BacktestEngine` instances. Each `BacktestEngine` is defined by a `BacktestRunConfig`. Multiple configurations can be bundled into a list and processed by the node in a single run.

Each **`BacktestRunConfig`** object consists of the following:

* A list of `BacktestDataConfig` objects.
* A list of `BacktestVenueConfig` objects.
* A list of `ImportableActorConfig` objects.
* A list of `ImportableStrategyConfig` objects.
* A list of `ImportableExecAlgorithmConfig` objects.
* An optional `ImportableControllerConfig` object.
* An optional `BacktestEngineConfig` object, with a default configuration if not specified.

In [178]:
import os
import sys
# Add src folder to Python path
root_path = os.path.abspath(os.path.join(os.getcwd(), ".."))
sys.path.append(root_path)

## Load data

In [179]:
import polars as pl
from src.utils.utils import polars_to_pandas
# from src.config import config

In [180]:
df = pl.read_parquet("../data/BTCUSDT_1h_tmp_365days.parquet")
df.head()

shape: (5, 12)
┌──────────────┬──────────┬──────────┬──────────┬───┬────────┬──────────────┬─────────────┬────────┐
│ open_time    ┆ open     ┆ high     ┆ low      ┆ … ┆ trades ┆ taker_base_v ┆ taker_quote ┆ ignore │
│ ---          ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---    ┆ ol           ┆ _vol        ┆ ---    │
│ datetime[ms] ┆ f64      ┆ f64      ┆ f64      ┆   ┆ i64    ┆ ---          ┆ ---         ┆ str    │
│              ┆          ┆          ┆          ┆   ┆        ┆ f64          ┆ f64         ┆        │
╞══════════════╪══════════╪══════════╪══════════╪═══╪════════╪══════════════╪═════════════╪════════╡
│ 2024-07-16   ┆ 63443.55 ┆ 63872.2  ┆ 63146.45 ┆ … ┆ 81332  ┆ 802.68075    ┆ 5.1057e7    ┆ 0      │
│ 11:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-07-16   ┆ 63746.11 ┆ 64265.33 ┆ 63601.02 ┆ … ┆ 101202 ┆ 928.07253    ┆ 5.9323e7    ┆ 0      │
│ 12:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-07-16   ┆ 63743.3  ┆ 64100.0  ┆ 63400.01 ┆ … ┆ 111397 ┆ 817.08425    ┆ 5.2132e7    ┆ 0      │
│ 13:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-07-16   ┆ 63419.99 ┆ 63898.71 ┆ 63063.83 ┆ … ┆ 119653 ┆ 879.26966    ┆ 5.5836e7    ┆ 0      │
│ 14:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-07-16   ┆ 63836.09 ┆ 64960.86 ┆ 63799.0  ┆ … ┆ 195247 ┆ 2100.49827   ┆ 1.3557e8    ┆ 0      │
│ 15:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
└──────────────┴──────────┴──────────┴──────────┴───┴────────┴──────────────┴─────────────┴────────┘

### POC design — Data ingest + catalog write

In [181]:
from __future__ import annotations
import polars as pl
from pathlib import Path
from nautilus_trader.model import BarType
from nautilus_trader.persistence.catalog import ParquetDataCatalog
from nautilus_trader.persistence.wranglers import BarDataWrangler
from nautilus_trader.test_kit.providers import TestInstrumentProvider
from decimal import Decimal

In [182]:
CATALOG_PATH = Path.cwd() / "catalog"
CATALOG_PATH.mkdir(parents=True, exist_ok=True)

# Create a catalog instance
catalog = ParquetDataCatalog(CATALOG_PATH)

In [183]:
BTCUSD = TestInstrumentProvider.btcusdt_binance()
print(BTCUSD)

CurrencyPair(id=BTCUSDT.BINANCE, raw_symbol=BTCUSDT, asset_class=CRYPTOCURRENCY, instrument_class=SPOT, quote_currency=USDT, is_inverse=False, price_precision=2, price_increment=0.01, size_precision=6, size_increment=0.000001, multiplier=1, lot_size=None, margin_init=0, margin_maint=0, maker_fee=0.001, taker_fee=0.001, info=None)


OBLIGATORIO: Pandas df con timestamp como indice

In [184]:
df = df.with_columns(
        (pl.col("open_time") + pl.duration(hours=1)).alias("timestamp"),
    ).to_pandas()

# Change order of columns
df = df.reindex(columns=["timestamp", "open", "high", "low", "close", "volume"])
df = df.set_index("timestamp")
df.head()

open      high       low     close      volume
timestamp                                                              
2024-07-16 12:00:00  63443.55  63872.20  63146.45  63746.11  1428.01869
2024-07-16 13:00:00  63746.11  64265.33  63601.02  63743.31  1785.10099
2024-07-16 14:00:00  63743.30  64100.00  63400.01  63419.99  1760.41084
2024-07-16 15:00:00  63419.99  63898.71  63063.83  63836.09  1780.20422
2024-07-16 16:00:00  63836.09  64960.86  63799.00  64878.24  3605.09775

In [185]:
EURUSD_SPOT_1HOUR_BARTYPE = BarType.from_str(
    f"{BTCUSD.id}-1-HOUR-LAST-EXTERNAL"
)

In [186]:
wrangler = BarDataWrangler(bar_type=EURUSD_SPOT_1HOUR_BARTYPE, instrument=BTCUSD)
BARS = wrangler.process(df)

In [187]:
catalog.write_data([BTCUSD])

In [188]:
catalog.write_data(BARS)

In [189]:
# Read and analyze data from the catalog
# - Retrieve all instrument definitions
all_instruments = catalog.instruments()
print(f"All instruments:\n{all_instruments}")

# - Get all available bars
all_bars = catalog.bars()
print(f"All bars count: {len(all_bars)}")

All instruments:
[CurrencyPair(id=BTCUSDT.BINANCE, raw_symbol=BTCUSDT, asset_class=CRYPTOCURRENCY, instrument_class=SPOT, quote_currency=USDT, is_inverse=False, price_precision=2, price_increment=0.01, size_precision=6, size_increment=0.000001, multiplier=1, lot_size=None, margin_init=0, margin_maint=0, maker_fee=0.001, taker_fee=0.001, info=None)]
All bars count: 8760


## Simple bt - High-Level API (BacktestNode)

In [190]:
from nautilus_trader.config import BacktestEngineConfig, BacktestDataConfig, BacktestVenueConfig, BacktestRunConfig
from nautilus_trader.backtest.node import BacktestNode
from nautilus_trader.model import Bar
from nautilus_trader.model import Money, Venue
from nautilus_trader.model.enums import OmsType
from nautilus_trader.model.enums import AccountType
from nautilus_trader.config import ImportableStrategyConfig
from nautilus_trader.model.currencies import BTC
from nautilus_trader.model.currencies import USDT

Configure Data

In [191]:
data_config = BacktestDataConfig(
        catalog_path = str(CATALOG_PATH),
        data_cls=Bar,
        instrument_id=BTCUSD.id,
        bar_types=[EURUSD_SPOT_1HOUR_BARTYPE],
    )
data_config

BacktestDataConfig(catalog_path='/Users/ezequielmrivero/git_tradelab/Crypto-Backtester-Duel/notebooks/catalog', data_cls=<class 'nautilus_trader.model.data.Bar'>, catalog_fs_protocol=None, catalog_fs_storage_options=None, instrument_id=InstrumentId('BTCUSDT.BINANCE'), start_time=None, end_time=None, filter_expr=None, client_id=None, metadata=None, bar_spec=None, instrument_ids=None, bar_types=[BarType(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL)])

Configure Venue

In [192]:
from nautilus_trader.adapters.binance import BINANCE_VENUE

# VENUE = Venue("BINANCE")

venue_config = BacktestVenueConfig(
        name=str(BINANCE_VENUE), #str(VENUE),
        oms_type="NETTING",
        account_type="CASH",  # Spot CASH account (not for perpetuals or futures)
        base_currency=None,  # Multi-currency account
        starting_balances=[Money(1_000_000.0, USDT), Money(1.0, BTC)],
    )
venue_config

BacktestVenueConfig(name='BINANCE', oms_type='NETTING', account_type='CASH', starting_balances=[Money(1000000.00000000, USDT), Money(1.00000000, BTC)], base_currency=None, default_leverage=1.0, leverages=None, book_type='L1_MBP', routing=False, frozen_account=False, reject_stop_orders=True, support_gtd_orders=True, support_contingent_orders=True, use_position_ids=True, use_random_ids=False, use_reduce_only=True, bar_execution=True, bar_adaptive_high_low_ordering=False, trade_execution=False, modules=None, fill_model=None, latency_model=None, fee_model=None)

Configure Strategy

In [193]:
strategies = [
    # ImportableStrategyConfig(
    #     strategy_path="nautilus_trader.examples.strategies.ema_cross:EMACross",
    #     config_path="nautilus_trader.examples.strategies.ema_cross:EMACrossConfig",
    #     config={
    #         "instrument_id": BTCUSD.id,
    #         "bar_type": EURUSD_SPOT_1HOUR_BARTYPE,
    #         "fast_ema_period": 30,
    #         "slow_ema_period": 100,
    #         "trade_size": Decimal("1"),
    #     },
    # ),
    ImportableStrategyConfig(
        strategy_path="src.strategies.nautilus:SmaCrossNT",
        config_path="src.strategies.nautilus:SmaCrossConfig",
        config={
            "instrument_id": BTCUSD.id,
            "bar_type": EURUSD_SPOT_1HOUR_BARTYPE,
            "fast_sma_period": 30,
            "slow_sma_period": 100,
            "trade_size": Decimal("0.1"),
        },
    ),
]
strategies

[ImportableStrategyConfig(strategy_path='src.strategies.nautilus:SmaCrossNT', config_path='src.strategies.nautilus:SmaCrossConfig', config={'instrument_id': InstrumentId('BTCUSDT.BINANCE'), 'bar_type': BarType(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL), 'fast_sma_period': 30, 'slow_sma_period': 100, 'trade_size': Decimal('0.1')})]

Configure Engine:

The BacktestDataConfig objects are integrated into the backtesting framework through BacktestRunConfig:
(https://nautilustrader.io/docs/latest/concepts/data/#integration-with-backtestrunconfig)

In [194]:
run_config = BacktestRunConfig(
    engine=BacktestEngineConfig(strategies=strategies),
    venues=[venue_config],
    data=[data_config],
)
run_config

BacktestRunConfig(venues=[BacktestVenueConfig(name='BINANCE', oms_type='NETTING', account_type='CASH', starting_balances=[Money(1000000.00000000, USDT), Money(1.00000000, BTC)], base_currency=None, default_leverage=1.0, leverages=None, book_type='L1_MBP', routing=False, frozen_account=False, reject_stop_orders=True, support_gtd_orders=True, support_contingent_orders=True, use_position_ids=True, use_random_ids=False, use_reduce_only=True, bar_execution=True, bar_adaptive_high_low_ordering=False, trade_execution=False, modules=None, fill_model=None, latency_model=None, fee_model=None)], data=[BacktestDataConfig(catalog_path='/Users/ezequielmrivero/git_tradelab/Crypto-Backtester-Duel/notebooks/catalog', data_cls=<class 'nautilus_trader.model.data.Bar'>, catalog_fs_protocol=None, catalog_fs_storage_options=None, instrument_id=InstrumentId('BTCUSDT.BINANCE'), start_time=None, end_time=None, filter_expr=None, client_id=None, metadata=None, bar_spec=None, instrument_ids=None, bar_types=[BarTy

In [ ]:
node = BacktestNode(configs=[run_config])

results = node.run()

2025-07-31T17:41:13.599561000Z [INFO] BACKTESTER-001.BacktestEngine: Building system kernel
2025-07-31T17:41:13.599575000Z [INFO] BACKTESTER-001.MessageBus: config.database=None
2025-07-31T17:41:13.599575001Z [INFO] BACKTESTER-001.MessageBus: config.encoding='msgpack'
2025-07-31T17:41:13.599576000Z [INFO] BACKTESTER-001.MessageBus: config.timestamps_as_iso8601=False
2025-07-31T17:41:13.599576001Z [INFO] BACKTESTER-001.MessageBus: config.buffer_interval_ms=None
2025-07-31T17:41:13.599577000Z [INFO] BACKTESTER-001.MessageBus: config.autotrim_mins=None
2025-07-31T17:41:13.599577001Z [INFO] BACKTESTER-001.MessageBus: config.use_trader_prefix=True
2025-07-31T17:41:13.599578000Z [INFO] BACKTESTER-001.MessageBus: config.use_trader_id=True
2025-07-31T17:41:13.599578001Z [INFO] BACKTESTER-001.MessageBus: config.use_instance_id=False
2025-07-31T17:41:13.599578002Z [INFO] BACKTESTER-001.MessageBus: config.streams_prefix='stream'
2025-07-31T17:41:13.599579000Z [INFO] BACKTESTER-001.MessageBus: con

2024-07-16T12:00:00.000000000Z [ERROR] BACKTESTER-001.SmaCrossNT: Received <Bar[0]> data for unknown bar type


ators to warm up [57]
2024-07-18T21:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,63555.00,63842.91,63438.21,63826.01,470.925870,1721336400000000000)
2024-07-18T21:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Waiting for indicators to warm up [58]
2024-07-18T22:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,63826.01,63905.73,63751.36,63850.00,358.865780,1721340000000000000)
2024-07-18T22:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Waiting for indicators to warm up [59]
2024-07-18T23:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,63849.99,64122.43,63714.00,64032.00,872.907780,1721343600000000000)
2024-07-18T23:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Waiting for indicators to warm up [60]
2024-07-19T00:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,64032.00,64090.00,63956.50,63987.92,32

1-002, account_id=BINANCE-001, trade_id=BINANCE-1-178, position_id=BTCUSDT.BINANCE-SmaCrossNT-000, order_side=SELL, order_type=MARKET, last_qty=0.100000, last_px=65_860.00 USDT, commission=6.58600000 USDT, liquidity_side=TAKER, ts_event=1721761200000000000)
2024-07-23T19:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: <--[EVT] PositionClosed(instrument_id=BTCUSDT.BINANCE, position_id=BTCUSDT.BINANCE-SmaCrossNT-000, account_id=BINANCE-001, opening_order_id=O-20240720-150000-001-000-1, closing_order_id=O-20240723-190000-001-000-2, entry=BUY, side=FLAT, signed_qty=0.0, quantity=0.000000, peak_qty=0.100000, currency=USDT, avg_px_open=66590.0, avg_px_close=65860.0, realized_return=-0.01096, realized_pnl=-86.24500000 USDT, unrealized_pnl=0.00000000 USDT, ts_opened=1721487600000000000, ts_last=1721761200000000000, ts_closed=1721761200000000000, duration_ns=273600000000000)
2024-07-23T20:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,65859.99,660

In [ ]:
from nautilus_trader.backtest.results import BacktestResult

node = BacktestNode(configs=[run_config])

# Runs one or many configs synchronously
results: list[BacktestResult] = node.run()

AST-EXTERNAL,66440.01,66560.01,66326.00,66379.99,663.878160,1722441600000000000)
2024-07-31T17:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,66379.99,66751.32,66287.87,66362.00,678.149560,1722445200000000000)
2024-07-31T18:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,66362.01,66836.30,66303.84,66686.00,716.249770,1722448800000000000)
2024-07-31T19:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,66686.01,66733.99,66138.00,66527.99,1237.290650,1722452400000000000)
2024-07-31T20:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,66527.99,66649.12,64957.14,65256.83,3777.683190,1722456000000000000)
2024-07-31T21:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,65256.83,65422.00,64543.57,64595.81,2050.405840,1722459600000000000)
2024-07-31T22:00:00.000000000Z [INFO] BACKTEST

:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,67750.00,67933.79,67688.14,67803.21,389.907190,1729548000000000000)
2024-10-21T23:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,67803.21,67878.78,67602.84,67781.07,544.894630,1729551600000000000)
2024-10-22T00:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,67781.07,67781.08,67366.66,67377.50,662.800130,1729555200000000000)
2024-10-22T01:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,67377.50,67406.50,66571.42,67149.73,2276.063780,1729558800000000000)
2024-10-22T02:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,67149.73,67538.00,67050.00,67508.29,826.669040,1729562400000000000)
2024-10-22T02:00:00.000000000Z [INFO] BACKTESTER-001.SmaCrossNT: Closing 1 open position
2024-10-22T02:00:00.000000000Z [INFO] BACKTESTER-001.

2024-07-16T12:00:00.000000000Z [ERROR] BACKTESTER-001.SmaCrossNT: Received <Bar[0]> data for unknown bar type


In [197]:
from nautilus_trader.backtest.engine import BacktestEngine

engine: BacktestEngine = node.get_engine(run_config.id)

account_report = pl.DataFrame(engine.trader.generate_account_report(BINANCE_VENUE))
orders_report = pl.DataFrame(engine.trader.generate_order_fills_report())
positions_report = pl.DataFrame(engine.trader.generate_positions_report())

In [198]:
account_report

shape: (210, 10)
┌────────────┬────────┬────────────┬──────────┬───┬────────────┬────────────┬──────────┬───────────┐
│ total      ┆ locked ┆ free       ┆ currency ┆ … ┆ base_curre ┆ margins    ┆ reported ┆ info      │
│ ---        ┆ ---    ┆ ---        ┆ ---      ┆   ┆ ncy        ┆ ---        ┆ ---      ┆ ---       │
│ str        ┆ str    ┆ str        ┆ str      ┆   ┆ ---        ┆ list[null] ┆ bool     ┆ struct[0] │
│            ┆        ┆            ┆          ┆   ┆ str        ┆            ┆          ┆           │
╞════════════╪════════╪════════════╪══════════╪═══╪════════════╪════════════╪══════════╪═══════════╡
│ 1000000.00 ┆ 0E-8   ┆ 1000000.00 ┆ USDT     ┆ … ┆ null       ┆ []         ┆ true     ┆ {}        │
│ 000000     ┆        ┆ 000000     ┆          ┆   ┆            ┆            ┆          ┆           │
│ 1.00000000 ┆ 0E-8   ┆ 1.00000000 ┆ BTC      ┆ … ┆ null       ┆ []         ┆ true     ┆ {}        │
│ 993334.341 ┆ 0E-8   ┆ 993334.341 ┆ USDT     ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 00000      ┆        ┆ 00000      ┆          ┆   ┆            ┆            ┆          ┆           │
│ 1.10000000 ┆ 0E-8   ┆ 1.10000000 ┆ BTC      ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 999913.755 ┆ 0E-8   ┆ 999913.755 ┆ USDT     ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 00000      ┆        ┆ 00000      ┆          ┆   ┆            ┆            ┆          ┆           │
│ …          ┆ …      ┆ …          ┆ …        ┆ … ┆ …          ┆ …          ┆ …        ┆ …         │
│ 1.00000000 ┆ 0E-8   ┆ 1.00000000 ┆ BTC      ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 990869.964 ┆ 0E-8   ┆ 990869.964 ┆ USDT     ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 76200      ┆        ┆ 76200      ┆          ┆   ┆            ┆            ┆          ┆           │
│ 1.10000000 ┆ 0E-8   ┆ 1.10000000 ┆ BTC      ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 1002530.24 ┆ 0E-8   ┆ 1002530.24 ┆ USDT     ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
│ 780700     ┆        ┆ 780700     ┆          ┆   ┆            ┆            ┆          ┆           │
│ 1.00000000 ┆ 0E-8   ┆ 1.00000000 ┆ BTC      ┆ … ┆ null       ┆ []         ┆ false    ┆ {}        │
└────────────┴────────┴────────────┴──────────┴───┴────────────┴────────────┴──────────┴───────────┘

In [199]:
orders_report

shape: (104, 31)
┌────────────┬────────────┬────────────┬────────────┬───┬──────┬───────────┬───────────┬───────────┐
│ trader_id  ┆ strategy_i ┆ instrument ┆ venue_orde ┆ … ┆ tags ┆ init_id   ┆ ts_init   ┆ ts_last   │
│ ---        ┆ d          ┆ _id        ┆ r_id       ┆   ┆ ---  ┆ ---       ┆ ---       ┆ ---       │
│ str        ┆ ---        ┆ ---        ┆ ---        ┆   ┆ str  ┆ str       ┆ datetime[ ┆ datetime[ │
│            ┆ str        ┆ str        ┆ str        ┆   ┆      ┆           ┆ ns, UTC]  ┆ ns, UTC]  │
╞════════════╪════════════╪════════════╪════════════╪═══╪══════╪═══════════╪═══════════╪═══════════╡
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 81f24c8c- ┆ 2024-07-2 ┆ 2024-07-2 │
│ -001       ┆ -000       ┆ NANCE      ┆ 001        ┆   ┆      ┆ b1ee-4523 ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -bc35-139 ┆ 15:00:00  ┆ 15:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ dcb…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 06013d2b- ┆ 2024-07-2 ┆ 2024-07-2 │
│ -001       ┆ -000       ┆ NANCE      ┆ 002        ┆   ┆      ┆ f237-47f9 ┆ 3         ┆ 3         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -8c42-8c9 ┆ 19:00:00  ┆ 19:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ ed3…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 0a72d879- ┆ 2024-07-2 ┆ 2024-07-2 │
│ -001       ┆ -000       ┆ NANCE      ┆ 003        ┆   ┆      ┆ 774f-4125 ┆ 6         ┆ 6         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -a746-2e8 ┆ 18:00:00  ┆ 18:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ ecf…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 1503908a- ┆ 2024-07-3 ┆ 2024-07-3 │
│ -001       ┆ -000       ┆ NANCE      ┆ 004        ┆   ┆      ┆ d361-4317 ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -9897-587 ┆ 10:00:00  ┆ 10:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ b1e…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ f7672a87- ┆ 2024-08-0 ┆ 2024-08-0 │
│ -001       ┆ -000       ┆ NANCE      ┆ 005        ┆   ┆      ┆ f9e0-4c93 ┆ 8         ┆ 8         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -8230-812 ┆ 05:00:00  ┆ 05:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ 7f0…      ┆ UTC       ┆ UTC       │
│ …          ┆ …          ┆ …          ┆ …          ┆ … ┆ …    ┆ …         ┆ …         ┆ …         │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ bd209c8e- ┆ 2025-07-0 ┆ 2025-07-0 │
│ -001       ┆ -000       ┆ NANCE      ┆ 100        ┆   ┆      ┆ 768b-4a92 ┆ 5         ┆ 5         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -b751-bca ┆ 13:00:00  ┆ 13:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ 52f…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 206a5536- ┆ 2025-07-0 ┆ 2025-07-0 │
│ -001       ┆ -000       ┆ NANCE      ┆ 101        ┆   ┆      ┆ 9a4f-4942 ┆ 7         ┆ 7         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -9e13-94b ┆ 09:00:00  ┆ 09:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ 136…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 6d9e6206- ┆ 2025-07-0 ┆ 2025-07-0 │
│ -001       ┆ -000       ┆ NANCE      ┆ 102        ┆   ┆      ┆ 522e-4a07 ┆ 8         ┆ 8         │
│            ┆            ┆            ┆            ┆   ┆      ┆ -95cf-c0d ┆ 15:00:00  ┆ 15:00:00  │
│            ┆            ┆            ┆            ┆   ┆      ┆ 1ff…      ┆ UTC       ┆ UTC       │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BIN

In [200]:
positions_report

shape: (52, 20)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ trader_id ┆ strategy_ ┆ instrumen ┆ account_i ┆ … ┆ avg_px_cl ┆ commissio ┆ realized_ ┆ realized │
│ ---       ┆ id        ┆ t_id      ┆ d         ┆   ┆ ose       ┆ ns        ┆ return    ┆ _pnl     │
│ str       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆ str       ┆ str       ┆ str       ┆   ┆ f64       ┆ list[str] ┆ f64       ┆ str      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 65860.0   ┆ ["13.2450 ┆ -0.01096  ┆ -86.2450 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 0000      ┆           ┆ 0000     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 66608.01  ┆ ["13.3980 ┆ -0.01134  ┆ -89.7970 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 0100      ┆           ┆ 0100     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 58403.76  ┆ ["11.5169 ┆ 0.02886   ┆ 152.3250 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 1000      ┆           ┆ 9000     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 58060.37  ┆ ["11.8921 ┆ -0.04602  ┆ -292.005 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 8700      ┆           ┆ 18700    │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 59011.99  ┆ ["11.8409 ┆ -0.00648  ┆ -50.3539 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 1100      ┆           ┆ 1100     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 104856.06 ┆ ["21.2036 ┆ -0.02168  ┆ -253.597 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 0600      ┆           ┆ 60600    │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 106556.39 ┆ ["21.2211 ┆ 0.00853   ┆ 68.89483 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 6200      ┆           ┆ 800 USDT │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆          │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 108148.57 ┆ ["21.7063 ┆ -0.00704  ┆ -98.3493 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 5700      ┆           ┆ 5700     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 108376.0  ┆ ["21.7387 ┆ -0.00583  ┆ -85.3087 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 7000      ┆           ┆ 7000     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ 116719.55 ┆ ["22.5609 ┆ 0.0719    ┆ 760.4040 │
│ R-001     ┆ T-000     ┆ INANCE    ┆ 01        ┆   ┆           ┆ 4500      ┆           ┆ 5500     │
│           ┆           ┆           ┆           ┆   ┆           ┆ USDT"]    ┆           ┆ USDT     │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘